In [1]:
import pandas as pd
from IPython.display import clear_output, Markdown, Math
import ipywidgets as widgets
import os
import glob
import json
import numpy as np
import itertools
import sklearn.utils as sku
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer, HashingVectorizer
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MultiLabelBinarizer

In [2]:
import sys
sys.path.append("..")

from Tools.Emoji_Distance import sentiment_vector_to_emoji
from Tools.Emoji_Distance import emoji_to_sentiment_vector

def emoji2sent(emoji_arr):
    return np.array([emoji_to_sentiment_vector(e) for e in emoji_arr])

def sent2emoji(sent_arr):
    return [sentiment_vector_to_emoji(s) for s in sent_arr]

In [3]:
SINGLE_LABEL = True

# simple twitter approach
*for learning emoji usage by single (in the meaning of unconnected) twitter messages*

## loading train data

In [4]:
data_root_folder = "./data_en/" # i created a symlink here

* get all json files in `data_root_folder`

In [5]:
json_files = sorted(glob.glob(data_root_folder + "/*.json"))

----

* so far, only load the first file

In [6]:
twitter_data = pd.read_json(json_files[0], encoding="utf-8")
twitter_data

EMOJI  \
0                           [🔥, 👏]   
1                              [🤦]   
2                              [😄]   
3                              [📷]   
4                           [😩, 😩]   
5                           [😭, 💓]   
6                              [😂]   
7                              [💯]   
8                              [🙄]   
9                        [😟, 😥, 😢]   
10                             [🌻]   
11                       [🍁, 🌺, 🍂]   
12                             [🍃]   
13                          [💭, 🤦]   
14                          [😍, 😘]   
15                             [😜]   
16                          [😂, 🔥]   
17                             [💕]   
18                             [😉]   
19                             [👅]   
20                          [👌, 🙂]   
21                          [🤗, 📺]   
22                             [💯]   
23                       [👅, 💦, 🍑]   
24                             [💔]   
25                       [🤐, 🤐, 🤐]   
26                             [😴]   
27                             [😂]   
28                          [😂, 🙄]   
29              [🎉, 🎂, 🎈, 🎊, 🎁, 💜]   
...                            ...   
68703                          [😕]   
68704                       [😂, 😩]   
68705                          [😂]   
68706                          [💖]   
68707                 [🌆, 👉, 🚖, 📞]   
68708                          [😁]   
68709                          [😋]   
68710                    [👌, 🎃, 😘]   
68711                          [👍]   
68712                          [😭]   
68713                          [😂]   
68714                    [😭, 😭, 💘]   
68715                       [😫, ✋]   
68716                       [😂, 🙁]   
68717                          [😭]   
68718                       [😢, 💔]   
68719                          [🙃]   
68720              [😂, 😂, 😂, 😂, 😂]   
68721                    [👌, 👊, 🙌]   
68722                          [😴]   
68723                 [😂, 😂, 😂, 😂]   
68724                          [😀]   
68725                          [😎]   
68726                          [✨]   
68727                          [🤷]   
68728                          [😘]   
68729                          [😂]   
68730                          [🙏]   
68731                          [💁]   
68732  [🍃, 🌻, 🌻, 🍃, 🍃, 💐, 💐, 🍃, 🙋]   

                                              HASHTAGS  \
0                                                   []   
1                                                   []   
2                                                   []   
3                                                   []   
4                                                   []   
5                                                   []   
6                                                   []   
7                                                   []   
8                                                   []   
9                                                   []   
10                                                  []   
11                                                  []   
12         [#mortdale, #partofthefamily, #gorgeousboy]   
13                                                  []   
14                                     [#7YearsOfKMH2]   
15                                                  []   
16                                                  []   
17                                                  []   
18                                                  []   
19                                 [#footfetishnation]   
20                                                  []   
21                                                  []   
22                                                  []   
23                                                  []   
24                                                  []   
25                                                  []   
26                                                  []   
27                                              

* extracting emojis and text

In [7]:
emojis = twitter_data['EMOJI']
plain_text = twitter_data['text']

* make our plain text more "plain":
    * removing the keyword `<EMOJI>` (just for the beginning)
    * removing remaining useless emojis, like skin modifier etc.

In [8]:
# defining blacklist for modifier emojis:
emoji_blacklist = set([
    chr(0x1F3FB),
    chr(0x1F3FC),
    chr(0x1F3FD),
    chr(0x1F3FE),
    chr(0x1F3FF),
    chr(0x2642),
    chr(0x2640)
])

In [9]:
# filtering them and the EMOJI keyword out:
plain_text = plain_text.str.replace("(<EMOJI>|<USER>|<HASHTAG>)","").str.replace("[" + "".join(list(emoji_blacklist)) + "]","")

* defining different criterias for choosing a single emoji (currently `latest` is used)

In [10]:
def latest(lst):
    return lst[-1] if len(lst) > 0 else 'X' 
def most_common(lst):
    # trying to find the most common used emoji in the given lst
    return max(set(lst), key=lst.count) if len(lst) > 0 else "X" # setting label to 'X' if there is an empty emoji list

* convert all emojis to a sentiment vector

In [11]:
labels = emoji2sent([latest(e) for e in emojis])


In [12]:
len(labels)

68733

In [13]:
wrong_labels = np.isnan(np.linalg.norm(labels, axis=1))

* remove all data we have no label for

In [14]:
labels = labels[np.invert(wrong_labels)]
plain_text = plain_text[np.invert(wrong_labels)]
emojis = emojis[np.invert(wrong_labels)]

In [15]:
print(len(labels), len(emojis), len(plain_text))

33368 33368 33368


* generate weights:

In [16]:
# at first count over our table
emoji_count = {}


for e_list in emojis:
    for e in set(e_list):
        if e not in emoji_count:
            emoji_count[e] = 0
        emoji_count[e] += 1

emoji_count
emoji_sum = sum([emoji_count[e] for e in emoji_count])

emoji_weights = {}
for e in emoji_count:
    # tfidf for emojis
    emoji_weights[e] = np.log((emoji_sum / emoji_count[e]))

weights_sum= sum([emoji_weights[x] for x in emoji_weights])
    
# normalize:
for e in emoji_weights:
    emoji_weights[e] = emoji_weights[e] / weights_sum

emoji_weights['X'] = 0  # dummy values
emoji_count['X'] = 0

* most used emojis in Dataset

In [17]:
import operator

In [18]:
sorted_emoji_count = list(reversed(sorted(emoji_count.items(), key=operator.itemgetter(1))))
display(sorted_emoji_count[:5])

top_emojis = [x[0] for x in sorted_emoji_count[:5]]
display(top_emojis)

[('😂', 10182), ('😭', 3893), ('😍', 2866), ('😩', 1647), ('😊', 1450)]

['😂', '😭', '😍', '😩', '😊']

* only learn the most used ones:

In [19]:
in_top = [sentiment_vector_to_emoji(x) in top_emojis for x in labels]
labels = labels[in_top]
plain_text = plain_text[in_top]
emojis = emojis[in_top]
print(len(labels), len(emojis), len(plain_text))

17815 17815 17815


* generating train and test set:

In [20]:
X1, Xt1, y1, yt1 = train_test_split(plain_text, labels, test_size=0.1, random_state=4222)

In [21]:
#y1_weights = np.array([(sum([emoji_weights[e] for e in e_list]) / len(e_list)) if len(e_list) > 0 else 0 for e_list in sent2emoji(y1)])

In [22]:
vectorizer = TfidfVectorizer(stop_words='english')
vec_train = vectorizer.fit_transform(X1)
vec_test = vectorizer.transform(Xt1)

* train. this can take a very long time...

In [23]:
from sklearn.neural_network import MLPClassifier as MLP
from sklearn.multiclass import OneVsRestClassifier as OVRC
from sklearn.tree import DecisionTreeClassifier as DTC

from keras.models import Sequential
from keras.layers import Dense

Using TensorFlow backend.


In [25]:
def train(max_size = 10000, layers=[(1024, 'relu'),(y1[0].shape[0],'softmax')], random_state=4222, ovrc=False, n_iter=5):
    
    model = Sequential()
    
    # build mlp layers:
    keras_layers = []
    first_layer = True
    for layer in layers:
        if first_layer:
            model.add(Dense(units=layer[0], activation=layer[1], input_dim=vectorizer.transform([" "])[0]._shape[1]))
            first_layer = False
        else:
            model.add(Dense(units=layer[0], activation=layer[1]))
    
    #mlp = MLPClassifier(layers=sknn_layers, random_state=random_state, verbose=True, n_iter=n_iter, batch_size=100)
    
    model.compile(loss='categorical_crossentropy',
              optimizer='sgd',
              metrics=['accuracy'],)
    
    clf = OVRC(model) if ovrc else model

    clf.fit(vec_train[:max_size].A, y1[:max_size], validation_split=0.2, epochs=n_iter)#, sample_weight=y1_weights[:max_size])
    
    return clf

In [27]:
clf = train(max_size=1000,layers=[(200, 'relu'),(200, 'relu'),(200, 'linear'),(y1[0].shape[0],'softmax')], n_iter=100)

Train on 800 samples, validate on 200 samples
Epoch 1/100
800/800 [==============================] - 1s 690us/step - loss: 1.0883 - acc: 0.6925 - val_loss: 1.0760 - val_acc: 0.7400
Epoch 2/100
800/800 [==============================] - 0s 527us/step - loss: 1.0732 - acc: 0.7150 - val_loss: 1.0628 - val_acc: 0.7400
Epoch 3/100
800/800 [==============================] - 0s 528us/step - loss: 1.0651 - acc: 0.7150 - val_loss: 1.0556 - val_acc: 0.7400
Epoch 4/100
800/800 [==============================] - 0s 534us/step - loss: 1.0610 - acc: 0.7150 - val_loss: 1.0515 - val_acc: 0.7400
Epoch 5/100
800/800 [==============================] - 0s 534us/step - loss: 1.0589 - acc: 0.7150 - val_loss: 1.0493 - val_acc: 0.7400
Epoch 6/100
800/800 [==============================] - 0s 511us/step - loss: 1.0579 - acc: 0.7150 - val_loss: 1.0481 - val_acc: 0.7400
Epoch 7/100
800/800 [==============================] - 0s 546us/step - loss: 1.0573 - acc: 0.7150 - val_loss: 1.0473 - val_acc: 0.7400
Epoch 8/1

KeyboardInterrupt: 

* make a prediction and store it in a csv file:

In [26]:
pred = clf.predict(vectorizer.transform(Xt1))

In [36]:
print(np.linalg.norm(np.var(pred, axis=0)))
print(np.linalg.norm(np.var(labels)))


8.1356275e-06
0.02568319204819897


In [28]:
# build a dataframe to visualize test results:
testlist = pd.DataFrame({'text': Xt1, 
                         'teacher': sent2emoji(yt1),
                         'teacher_sentiment': yt1.tolist(),
                         'predict': sent2emoji(pred),
                         'predicted_sentiment': pred.tolist()})

In [36]:
display(testlist)


text teacher  \
7618                       There's fucking snow outside        😒   
6910    You look so animated bro! *Rimshot*, Get it? ...       😂   
35783                  Jon ordered it from a restaurant        😭   
15623           I just want to move back in with my mom        😅   
12023                                 guys lets vote!!!        😭   
15763             Bruhhhh this man need a show ASAP!!!         😂   
57240                   AND THE RICH SIT IN A LOW PLACE        😎   
2418                                  Time to go to bed        😂   
66384  May sound like a hillbilly, but girls that can...       😍   
44639                                          IM DYING        😂   
54463  Black forest hot chocolate is coming back to C...       🙌   
38407                               5 days till my 21st.       😎   
31342   I'm just going to leave my Twitter acct open ...       😄   
41255                                Oh god im so happy        😂   
19686                                        In my head        😭   
67193    Jo, chilllllllll. This kid is mentally beati...       😂   
40650                                    I’m ready sis         😇   
64416  Sometimes we need to know how to respect our p...       😊   
19525                                           Right?         🙆   
39024             priceless  love how  got back at you         😂   
35342                                             Right        😫   
9715                                   Opo pang i will!        😇   
40490   WOW  whomever was tasked with vetting applica...       😮   
22064                                     Thank you  !         😍   
53563  Dat  daurin Dan kwali from behind is the real ...       😄   
67332                          I miss my baby so much ♥️       😪   
15404  alright i'm gonna go take a shower, let me kno...       😕   
30130                  and neither are buying her music        😳   
37242   I saw that too as well! I feel to have it dur...       😂   
30533   I had a mental break down but I’m back like hey        😂   
...                                                  ...     ...   
16955           Bless up Esquivel finally update aeries        🙏   
36805             Look just like my Mizuno I had in ‘88        😂   
56326           This felt like it happened yesterday.          😢   
40306  Our Guest photo this week highlights the beaut...       😍   
51333  I need to see what “the stranger things” is ab...       😌   
42339   Plz can u make me a pc I don’t have enough mo...       😔   
7644                                  this is insulting        😧   
13953  I know this might sound crazy but I rather Don...       😐   
26460           Just a couple of cute pugs hanging out         😛   
31571   She knows nothing will happen to her.. welcom...       😒   
9536                                       happy raisin        😭   
19571                               I'm so disappointed        😡   
35934                                        Nailed it.        😂   
4605                          oh it’s more than a thing!       😂   
1913                                             stop it       😭   
11827                              Have an awesome  ❤️         😄   
15181                              when I see elbows ?         😂   
32869  Damn Jani back at it again with the BB-8 costu...       😹   
40784  I think a big part of the reason Nick Wilde is...       😻   
18611  My 12 year old brother on Altuve- “he’s like t...       😂   
28341          Bruh  like how she know the exact number?       😂   
41368                              They starting early         😂   
35554                              Please come through         😩   
27968                                         Thank you        😍   
36772            Imagine if the Vikings had a top 10 QB        😳   
7568                       Le costume de cupcakke.......       😭   
62837                           aM FKXNSK SCREAMING ODM        😂   
34105                              My bi

In [61]:
testlist.to_csv('test.csv')

* a simple output widget for testing:

In [63]:
out = widgets.Output()

t = widgets.Text()
b = widgets.Button(
    description='get smiley',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Click me',
    icon='check'
)



def handle_submit(sender):
    with out:
        clear_output()
    with out:
        pred = clf.predict(vectorizer.transform([t.value]))
        
        display(Markdown("# " + str(sent2emoji(pred))))

b.on_click(handle_submit)
    
display(t)
display(widgets.VBox([b, out]))  

Text(value='')

VBox(children=(Button(description='get smiley', icon='check', style=ButtonStyle(), tooltip='Click me'), Output()))

In [ ]:
import numpy as np

y_trans = mlb.inverse_transform(yt1)
pred_trans = mlb.inverse_transform(yt1)

# evaluate accuracy
pos = 0
neg = 0
all = 0
for entry in range(len(y_trans)):
    if len(np.intersect1d(y_trans[entry], pred_trans[entry])) > 0:
        pos += 1
    else:
        neg += 1
    all += 1
print(pos/all)
print(neg)